In [2]:
import random
import numpy as np
import pandas as pd
from copy import copy, deepcopy
from scipy.optimize import minimize
import itertools

import plotly
import plotly.graph_objs as go

import plotly.express as px
from plotly.subplots import make_subplots

from pathlib import Path
import json
import os

import sys
import time

In [174]:
# Возвращает функцию гаусса с заданными параметрами
def get_gaus_f(x,y,d):
    return lambda t: y*np.exp(-(t-x)**2/2/d**2)



# Сортирует информацию о гауссах в решении в возрастающем порядке
# На вход - матрица решений [[x1,A1,disp1], ...]
# На выход - отсортированная матрица по x [[xn,An,dispn], ...]
def Sort_gaus(v_sol):
    m_sol = np.array(v_sol).reshape(-1,3)
    m_sol = np.array(sorted(m_sol, key = lambda gaus: gaus[0]))
    v_sol_sorted = m_sol.reshape(-1).tolist()
    return v_sol_sorted


# Возвращает спектр по параметрам гауссовых кривых
def EvalSol(sol, l_wavelength = np.linspace(0 ,1 , 1024), add_noise_disp = 0, mult_noise_disp = 0, seed=None):
    X = l_wavelength
    spec = np.zeros(len(X))
    for n_gaus in range(0,len(sol), 3):
        f_gaus = get_gaus_f(sol[n_gaus], sol[n_gaus+1], sol[n_gaus+2])
        spec += np.array([f_gaus(t) for t in X])

    #Добавление шума
    random.seed(seed)
    add_spec_noise = np.random.normal(0, add_noise_disp, len(X))
    mult_spec_noise = np.random.normal(0, mult_noise_disp, len(X)) * spec
    spec = spec + add_spec_noise + mult_spec_noise

    return spec, X
    

# Рисует оба спектра и гауссианы
def DrawApprox(l_spec_1, l_spec_2, l_wavelength = np.linspace(0 ,1 , 1024), sol = np.array([])):
    fig = go.Figure()
    fig.update_layout(title_text="Spectrum",
                      title_font_size=20)
    
    K = l_wavelength
    fig.add_trace(go.Scatter(x=K,
                             y=l_spec_1,
                             name='1-st spec'))
    fig.add_trace(go.Scatter(x=K,
                             y=l_spec_2,
                             name='2-nd spec'))
    
    l_color = ['LimeGreen', 'MediumSlateBlue', 'Orange', 'DeepSkyBlue']
    i=0
    if len(sol) > 0:
        for n_gaus in range(0,len(sol), 3):
            f_gaus = get_gaus_f(sol[n_gaus], sol[n_gaus+1], sol[n_gaus+2])
            fig.add_vline(x=sol[n_gaus], line_width=2, line_color=l_color[i])
            fig.add_trace(go.Scatter(x=K,
                          y=[f_gaus(t) for t in K],
                          name=f'{n_gaus//3+1} gauss'))
            i+=1
    fig.show()
    return 


# Возвращает функцию Err(список-решение)
def GetFuncErr(spec, l_wavelength = np.linspace(0 ,1 , 1024)):
    F_err = lambda sol: np.sum((spec - EvalSol(sol)[0])**2)

    return F_err


def Grad_desc(f_Err, bounds, x0=None):
    if x0==None:
        x0=[]
        for a, b in bounds:
            x0.append(np.random.uniform(a,b))
        x0=np.array(x0)
        #print(f'x0: {x0}')

    res = minimize(f_Err, x0 = x0, bounds = bounds, method = 'SLSQP', options={'ftol':0})

    sol = res.x.tolist()
    f_err = f_Err(sol)

    return sol, f_err

In [71]:
disp_g = 0.1
ampl_gaus_noise = 0#0.2
add_noise_disp = 0.05

sol_1 = [0.3, 0.6, disp_g, 
         0.5, 0.8, disp_g,
         0.7, 0.7, disp_g,
         0.5, ampl_gaus_noise, 0.3]

points_spec_1, X = EvalSol(sol_1, add_noise_disp=add_noise_disp, seed=1)

F_err = GetFuncErr(points_spec_1, X)

bounds = [[0,1], [0,1], [0,1], 
          [0,1], [0,1], [0,1],
          [0,1], [0,1], [0,1]]

sol_2, fin_err = Grad_desc(f_Err=F_err, bounds=bounds, x0=sol_1[:-3])

print(f'fin_err: {fin_err}\tsol: {sol_2}')

points_spec_2, X = EvalSol(sol_2)


DrawApprox(points_spec_1, points_spec_2, X, sol_2)
DrawApprox(points_spec_1, points_spec_2, X, sol_1)

C:\Users\Gavriil\AppData\Local\Temp\ipykernel_10008\885390838.py:3: RuntimeWarning:

invalid value encountered in scalar divide

C:\Users\Gavriil\AppData\Local\Temp\ipykernel_10008\885390838.py:3: RuntimeWarning:

divide by zero encountered in scalar divide



fin_err: 2.4877651889572623	sol: [0.2829849286458349, 0.5112310854107261, 0.09274418764915425, 0.4996099163660063, 0.8840925354141446, 0.11755418144798982, 0.7131143392223932, 0.6125584393671919, 0.09499323307597793]


# Эксперимент

In [226]:
def exper(init_sol, bounds, x0=None, 
          add_noise_disp = 0, mult_noise_disp = 0, seed=None):
    '''Решение задачи, созданной гауссианами в init_sol.
    '''
    init_spec, X = EvalSol(init_sol, 
                           l_wavelength=np.linspace(0,1,1024), 
                           add_noise_disp = add_noise_disp, 
                           mult_noise_disp = mult_noise_disp, 
                           seed=seed)
    F_err = GetFuncErr(init_spec, X)

    sol, fin_err = Grad_desc(f_Err=F_err, bounds=bounds, x0=x0)

    return sol, fin_err


def mult_exper(disp_g, ampl_gaus_noise, bounds, add_noise_disp = 0, mult_noise_disp = 0, seed=None, num_launches=1):
    '''Проводит поиск решения c заданными дисперсиями гауссовых кривых и уровнем гауссового шумом.
    С помощью нескольких запусков.
    '''
    init_sol = [0.3, 0.6, disp_g, 
                0.5, 0.8, disp_g,
                0.7, 0.7, disp_g,
                0.5, ampl_gaus_noise, 0.3]
    
    print(f'\n=== disp_g: {disp_g}\tampl_noise: {ampl_gaus_noise} ===')

    best_sol, best_fin_err = exper(init_sol, bounds, x0=init_sol[:-3], # 0-guess
                                   add_noise_disp = add_noise_disp, mult_noise_disp = mult_noise_disp, seed=seed)
    for i in range(num_launches):
        sol, fin_err = exper(init_sol, bounds,
                             add_noise_disp = add_noise_disp, mult_noise_disp = mult_noise_disp, seed=seed)
        #print(f'{i}.\terr: {fin_err}\tx0: {sol}')
        if fin_err<best_fin_err:
            best_sol, best_fin_err = sol, fin_err
    print(f'= best_fin_err: {best_fin_err} =')


    return best_sol, best_fin_err


def mult_exper_2fit(disp_g, ampl_gaus_noise, bounds, add_noise_disp = 0, mult_noise_disp = 0, seed=None, num_launches=1):
    '''Проводит поиск решения c заданными дисперсиями гауссовых кривых и аддитивным шумом.
    С помощью нескольких запусков.Возвращает невязку решения с исходным спектром с шумом и без шума.
    '''
    init_sol = [0.3, 0.6, disp_g, 
                0.5, 0.8, disp_g,
                0.7, 0.7, disp_g,
                0.5, ampl_gaus_noise, 0.3]
    
    print(f'\n=== disp_g: {disp_g}\tadd_noise: {add_noise_disp} ===')

    best_sol, best_fin_err = exper(init_sol, bounds, x0=init_sol[:-3], # 0-guess
                                   add_noise_disp = add_noise_disp, mult_noise_disp = mult_noise_disp, seed=seed)
    for i in range(num_launches):
        sol, fin_err = exper(init_sol, bounds,
                             add_noise_disp = add_noise_disp, mult_noise_disp = mult_noise_disp, seed=seed)
        #print(f'{i}.\terr: {fin_err}\tx0: {sol}')
        if fin_err<best_fin_err:
            best_sol, best_fin_err = sol, fin_err
    print(f'= best_fin_err: {best_fin_err} =')

    init_spec_no_noise, X = EvalSol(init_sol)
    F_err = GetFuncErr(init_spec_no_noise, X)
    best_fin_err_no_noise = F_err(best_sol)
    print(f'= best_fin_err_no_noise: {best_fin_err_no_noise} =')

    return best_sol, best_fin_err, best_fin_err_no_noise


def mult_exper_3(disp_g, ampl_gaus_noise, bounds, add_noise_disp = 0, mult_noise_disp = 0, seed=None, num_launches=1):
    '''Проводит поиск решения c заданными дисперсиями гауссовых кривых и аддитивным шумом.
    С помощью нескольких запусков. Возвращает невязку решения с исходным спектром с шумом и без шума, а также delta_x, delta_y, delta_s.
    '''
    init_sol = [0.3, 0.6, disp_g, 
                0.5, 0.8, disp_g,
                0.7, 0.7, disp_g,
                0.5, ampl_gaus_noise, 0.3]
    
    print(f'\n=== disp_g: {disp_g}\tampl_noise: {ampl_gaus_noise}\tadd_noise: {add_noise_disp} ===')

    best_sol, best_fin_err = exper(init_sol, bounds, x0=init_sol[:-3], # 0-guess
                                   add_noise_disp = add_noise_disp, mult_noise_disp = mult_noise_disp, seed=seed)
    best_sol, best_fin_err = None, np.inf
    for i in range(num_launches):
        sol, fin_err = exper(init_sol, bounds,
                             add_noise_disp = add_noise_disp, mult_noise_disp = mult_noise_disp, seed=seed)
        #print(f'{i}.\terr: {fin_err}\tx0: {sol}')
        if fin_err<best_fin_err:
            best_sol, best_fin_err = sol, fin_err
    print(f'= best_fin_err: {best_fin_err} =')

    init_spec_no_noise, X = EvalSol(init_sol[:-3])
    F_err = GetFuncErr(init_spec_no_noise, X)
    best_fin_err_no_noise = F_err(best_sol)
    print(f'= best_fin_err_no_noise: {best_fin_err_no_noise} =')

    best_sol_sorted = Sort_gaus(best_sol)
    #print(np.array(best_sol)-np.array(init_sol[:-3]))
    delta_x, delta_y, delta_s = (np.abs(np.array(best_sol_sorted)-np.array(init_sol[:-3]))).reshape([-1,3]).mean(axis=0)

    return best_sol_sorted, best_fin_err, best_fin_err_no_noise, delta_x, delta_y, delta_s

In [201]:
a = np.array([1,2,3,4,5,6])

a.reshape([-1,3]).mean(axis=0)

array([2.5, 3.5, 4.5])

# 1-е приближение

In [39]:
'''l_disp_g = [0.1, 0.2, 0.3]
l_ampl_noise = [0.05, 0.1, 0.15, 0.2]
'''

l_disp_g = np.linspace(0.01, 0.12, 16)
l_ampl_noise = np.linspace(0.01, 0.2, 16)

bounds = [[0,1], [0,1], [0,1], 
          [0,1], [0,1], [0,1],
          [0,1], [0,1], [0,1]]


l_errors = []

for disp_g, ampl_noise in itertools.product(l_disp_g, l_ampl_noise):
    best_sol, best_fin_err = mult_exper(disp_g, ampl_noise, bounds = bounds, num_launches=3)
    l_errors.append(best_fin_err)

m_errors = np.array(l_errors).reshape(len(l_disp_g), len(l_ampl_noise))


=== disp_g: 0.01	ampl_noise: 0.01 ===


C:\Users\Gavriil\AppData\Local\Temp\ipykernel_10008\885390838.py:3: RuntimeWarning:

divide by zero encountered in scalar divide

C:\Users\Gavriil\AppData\Local\Temp\ipykernel_10008\885390838.py:3: RuntimeWarning:

invalid value encountered in scalar divide



= best_fin_err: 0.040894765438473674 =

=== disp_g: 0.01	ampl_noise: 0.02266666666666667 ===
= best_fin_err: 0.20936576877344293 =

=== disp_g: 0.01	ampl_noise: 0.035333333333333335 ===
= best_fin_err: 0.5068655940705222 =

=== disp_g: 0.01	ampl_noise: 0.048 ===
= best_fin_err: 0.9317999007937395 =

=== disp_g: 0.01	ampl_noise: 0.06066666666666667 ===
= best_fin_err: 1.4824222633712736 =

=== disp_g: 0.01	ampl_noise: 0.07333333333333332 ===
= best_fin_err: 2.156804708307881 =

=== disp_g: 0.01	ampl_noise: 0.086 ===
= best_fin_err: 2.9527994407743945 =

=== disp_g: 0.01	ampl_noise: 0.09866666666666667 ===
= best_fin_err: 3.8679879897245386 =

=== disp_g: 0.01	ampl_noise: 0.11133333333333333 ===
= best_fin_err: 4.899611785963911 =

=== disp_g: 0.01	ampl_noise: 0.12399999999999999 ===
= best_fin_err: 6.044474222743994 =

=== disp_g: 0.01	ampl_noise: 0.13666666666666666 ===
= best_fin_err: 7.298796677908592 =

=== disp_g: 0.01	ampl_noise: 0.14933333333333335 ===
= best_fin_err: 8.657995287

In [40]:
fig = px.imshow((m_errors),
                labels=dict(y="disp_g", x="ampl_noise", color="Error"),
                y=l_disp_g,
                x=l_ampl_noise)

fig.show()

In [41]:
disp_g = 0.024666
ampl_gaus_noise = 0.2#0.01

init_sol = [0.3, 0.6, disp_g, 
            0.5, 0.8, disp_g,
            0.7, 0.7, disp_g,
            0.5, ampl_gaus_noise, 0.3]

bounds = [[0,1], [0,1], [0,1], 
          [0,1], [0,1], [0,1],
          [0,1], [0,1], [0,1]]

sol, fin_err = mult_exper(disp_g, ampl_noise, bounds = bounds, num_launches=3)


print(f'fin_err: {fin_err}\tsol: {sol}')

init_spec, X = EvalSol(init_sol)
fin_spec, X = EvalSol(sol)
DrawApprox(init_spec, fin_spec, X, sol)
DrawApprox(init_spec, fin_spec, X, init_sol)


=== disp_g: 0.024666	ampl_noise: 0.2 ===


C:\Users\Gavriil\AppData\Local\Temp\ipykernel_10008\885390838.py:3: RuntimeWarning:

divide by zero encountered in scalar divide

C:\Users\Gavriil\AppData\Local\Temp\ipykernel_10008\885390838.py:3: RuntimeWarning:

invalid value encountered in scalar divide



= best_fin_err: 6.280156281129946 =
fin_err: 6.280156281129946	sol: [0.3020839222625719, 0.6623648938589183, 0.040941017924374754, 0.5000984659043614, 0.8972081977353578, 0.03778252249478606, 0.6984110138286747, 0.7722207937209637, 0.03720029149157594]


# 2-е приближение. Аддитивный шум

In [75]:
'''l_disp_g = [0.1, 0.2, 0.3]
l_ampl_noise = [0.05, 0.1, 0.15, 0.2]
'''

l_disp_g = np.linspace(0.01, 0.12, 5)
ampl_gaus_noise = 0
l_add_noise_disp = np.linspace(0.001, 0.05, 5)

bounds = [[0,1], [0,1], [0,1], 
          [0,1], [0,1], [0,1],
          [0,1], [0,1], [0,1]]


l_errors = []
l_errors_no_noise = []

for disp_g, add_noise_disp in itertools.product(l_disp_g, l_add_noise_disp):
    best_sol, best_fin_err, best_fin_err_no_noise = mult_exper_2fit(disp_g, ampl_gaus_noise, bounds = bounds, add_noise_disp = add_noise_disp, num_launches=3)
    l_errors.append(best_fin_err)
    l_errors_no_noise.append(best_fin_err_no_noise)

m_errors = np.array(l_errors).reshape(len(l_disp_g), len(l_add_noise_disp))
m_errors_no_noise = np.array(l_errors_no_noise).reshape(len(l_disp_g), len(l_add_noise_disp))


=== disp_g: 0.01	ampl_noise: 0 ===


C:\Users\Gavriil\AppData\Local\Temp\ipykernel_10008\885390838.py:3: RuntimeWarning:

divide by zero encountered in scalar divide

C:\Users\Gavriil\AppData\Local\Temp\ipykernel_10008\885390838.py:3: RuntimeWarning:

invalid value encountered in scalar divide



= best_fin_err: 0.00108416214856475 =
= best_fin_err_no_noise: 1.7124578444125024e-05 =

=== disp_g: 0.01	ampl_noise: 0 ===
= best_fin_err: 0.1829009639641873 =
= best_fin_err_no_noise: 0.0011676399509412342 =

=== disp_g: 0.01	ampl_noise: 0 ===
= best_fin_err: 0.6152732922500777 =
= best_fin_err_no_noise: 0.0024239820632319968 =

=== disp_g: 0.01	ampl_noise: 0 ===
= best_fin_err: 1.3393404921772645 =
= best_fin_err_no_noise: 0.006632676965863841 =

=== disp_g: 0.01	ampl_noise: 0 ===
= best_fin_err: 2.545354991622027 =
= best_fin_err_no_noise: 0.029210921389911576 =

=== disp_g: 0.0375	ampl_noise: 0 ===
= best_fin_err: 0.0010294472943406237 =
= best_fin_err_no_noise: 5.006825480212525e-06 =

=== disp_g: 0.0375	ampl_noise: 0 ===
= best_fin_err: 5.9021903530648315e-12 =
= best_fin_err_no_noise: 5.9021903530648315e-12 =

=== disp_g: 0.0375	ampl_noise: 0 ===
= best_fin_err: 5.903650189195718e-12 =
= best_fin_err_no_noise: 5.903650189195718e-12 =

=== disp_g: 0.0375	ampl_noise: 0 ===
= best

ValueError: cannot reshape array of size 25 into shape (5,16)

In [76]:
m_errors = np.array(l_errors).reshape(len(l_disp_g), len(l_add_noise_disp))
m_errors_no_noise = np.array(l_errors_no_noise).reshape(len(l_disp_g), len(l_add_noise_disp))

In [78]:
fig = px.imshow((m_errors),
                labels=dict(y="disp_g", x="add_noise_disp", color="Error"),
                y=l_disp_g,
                x=l_add_noise_disp)

fig.show()

fig = px.imshow((m_errors_no_noise),
                labels=dict(y="disp_g", x="add_noise_disp", color="Error"),
                y=l_disp_g,
                x=l_add_noise_disp)

fig.show()

# 3-е приближение

In [82]:
'''l_disp_g = [0.1, 0.2, 0.3]
l_ampl_noise = [0.05, 0.1, 0.15, 0.2]
'''

l_disp_g = np.linspace(0.01, 0.12, 16)
ampl_gaus_noise = 0
l_add_noise_disp = np.linspace(0.001, 0.05, 16)

bounds = [[0,1], [0,1], [0,1], 
          [0,1], [0,1], [0,1],
          [0,1], [0,1], [0,1]]


l_errors = []
l_errors_no_noise = []

for disp_g, add_noise_disp in itertools.product(l_disp_g, l_add_noise_disp):
    best_sol, best_fin_err, best_fin_err_no_noise = mult_exper_2fit(disp_g, ampl_gaus_noise, bounds = bounds, add_noise_disp = add_noise_disp, num_launches=3)
    l_errors.append(best_fin_err)
    l_errors_no_noise.append(best_fin_err_no_noise)

m_errors = np.array(l_errors).reshape(len(l_disp_g), len(l_add_noise_disp))
m_errors_no_noise = np.array(l_errors_no_noise).reshape(len(l_disp_g), len(l_add_noise_disp))


=== disp_g: 0.01	add_noise: 0.001 ===


C:\Users\Gavriil\AppData\Local\Temp\ipykernel_10008\885390838.py:3: RuntimeWarning:

divide by zero encountered in scalar divide

C:\Users\Gavriil\AppData\Local\Temp\ipykernel_10008\885390838.py:3: RuntimeWarning:

invalid value encountered in scalar divide



= best_fin_err: 0.0010192690633001845 =
= best_fin_err_no_noise: 7.179628727283683e-06 =

=== disp_g: 0.01	add_noise: 0.004266666666666667 ===
= best_fin_err: 0.018331269200874845 =
= best_fin_err_no_noise: 0.00014631251806613253 =

=== disp_g: 0.01	add_noise: 0.007533333333333334 ===
= best_fin_err: 0.052211621616413004 =
= best_fin_err_no_noise: 0.0002961096759140579 =

=== disp_g: 0.01	add_noise: 0.0108 ===
= best_fin_err: 0.10684480032786395 =
= best_fin_err_no_noise: 0.00036564853707077137 =

=== disp_g: 0.01	add_noise: 0.014066666666666668 ===
= best_fin_err: 0.1933711126642895 =
= best_fin_err_no_noise: 0.001092682201915146 =

=== disp_g: 0.01	add_noise: 0.017333333333333336 ===
= best_fin_err: 0.2886788275923621 =
= best_fin_err_no_noise: 0.0013821606657801943 =

=== disp_g: 0.01	add_noise: 0.0206 ===
= best_fin_err: 0.4290373790057401 =
= best_fin_err_no_noise: 0.002838329466982798 =

=== disp_g: 0.01	add_noise: 0.023866666666666668 ===
= best_fin_err: 0.5712843264430677 =
= b

In [83]:
fig = px.imshow((m_errors),
                labels=dict(y="disp_g", x="add_noise_disp", color="Error"),
                y=l_disp_g,
                x=l_add_noise_disp)

fig.show()

fig = px.imshow((m_errors_no_noise),
                labels=dict(y="disp_g", x="add_noise_disp", color="Error"),
                y=l_disp_g,
                x=l_add_noise_disp)

fig.show()

In [102]:
trash_hold = 0.14
m_errors_no_noise_1 = np.multiply(m_errors_no_noise, (m_errors_no_noise<trash_hold))

fig = px.imshow((m_errors_no_noise_1),
                labels=dict(y="disp_g", x="add_noise_disp", color="Error"),
                y=l_disp_g,
                x=l_add_noise_disp)

fig.show()

In [107]:
disp_g = 0.1
ampl_gaus_noise = 0
add_noise_disp = 0.001

init_sol = [0.3, 0.6, disp_g, 
            0.5, 0.8, disp_g,
            0.7, 0.7, disp_g,
            0.5, ampl_gaus_noise, 0.3]

bounds = [[0,1], [0,1], [0,1], 
          [0,1], [0,1], [0,1],
          [0,1], [0,1], [0,1]]

sol, fin_err, fin_err_no_noise = mult_exper_2fit(disp_g, ampl_gaus_noise, bounds = bounds, add_noise_disp = add_noise_disp, num_launches=3)


print(f'fin_err: {fin_err}\fin_err_no_noise: {fin_err_no_noise}\tsol: {sol}')

init_spec, X = EvalSol(init_sol, add_noise_disp=add_noise_disp)
fin_spec, X = EvalSol(sol)
DrawApprox(init_spec, fin_spec, X, sol)
DrawApprox(init_spec, fin_spec, X, init_sol)


=== disp_g: 0.1	add_noise: 0.001 ===


C:\Users\Gavriil\AppData\Local\Temp\ipykernel_10008\885390838.py:3: RuntimeWarning:

invalid value encountered in scalar divide

C:\Users\Gavriil\AppData\Local\Temp\ipykernel_10008\885390838.py:3: RuntimeWarning:

divide by zero encountered in scalar divide



= best_fin_err: 0.001045871895259753 =
= best_fin_err_no_noise: 1.4824912569995825e-05 =
fin_err: 0.001045871895259753in_err_no_noise: 1.4824912569995825e-05	sol: [0.29980870467523063, 0.5990770675731305, 0.09997542851356307, 0.5001798189737472, 0.8020701154650146, 0.10026331589078732, 0.7003737519252308, 0.6981118551923036, 0.09983056436085286]


# 4-е приближение.
Пробую нижнюю часть от 3-ей попытки

In [146]:
'''l_disp_g = [0.1, 0.2, 0.3]
l_ampl_noise = [0.05, 0.1, 0.15, 0.2]
'''

l_disp_g = np.linspace(0.06, 0.12, 16)
ampl_gaus_noise = 0
l_add_noise_disp = np.linspace(0, 0.05, 16)

bounds = [[0,1], [0,1], [0,1], 
          [0,1], [0,1], [0,1],
          [0,1], [0,1], [0,1]]


l_errors = []
l_errors_no_noise = []
l_delta_x, l_delta_y, l_delta_s = [],[],[]

for disp_g, add_noise_disp in itertools.product(l_disp_g, l_add_noise_disp):
    best_sol, best_fin_err, best_fin_err_no_noise, delta_x, delta_y, delta_s = mult_exper_3(disp_g, ampl_gaus_noise, bounds = bounds, add_noise_disp = add_noise_disp, num_launches=3)
    l_errors.append(best_fin_err)
    l_errors_no_noise.append(best_fin_err_no_noise)

    l_delta_x.append(delta_x)
    l_delta_y.append(delta_y)
    l_delta_s.append(delta_s)

m_errors = np.array(l_errors).reshape(len(l_disp_g), len(l_add_noise_disp))
m_errors_no_noise = np.array(l_errors_no_noise).reshape(len(l_disp_g), len(l_add_noise_disp))

m_delta_x = np.array(l_delta_x).reshape(len(l_disp_g), len(l_add_noise_disp))
m_delta_y = np.array(l_delta_y).reshape(len(l_disp_g), len(l_add_noise_disp))
m_delta_s = np.array(l_delta_s).reshape(len(l_disp_g), len(l_add_noise_disp))


=== disp_g: 0.06	add_noise: 0.0 ===


C:\Users\Gavriil\AppData\Local\Temp\ipykernel_10008\885390838.py:3: RuntimeWarning:

invalid value encountered in scalar divide

C:\Users\Gavriil\AppData\Local\Temp\ipykernel_10008\885390838.py:3: RuntimeWarning:

divide by zero encountered in scalar divide



= best_fin_err: 9.130199806989465e-15 =
= best_fin_err_no_noise: 9.130199806989465e-15 =

=== disp_g: 0.06	add_noise: 0.0033333333333333335 ===
= best_fin_err: 0.010716517701443655 =
= best_fin_err_no_noise: 7.415656928943611e-05 =

=== disp_g: 0.06	add_noise: 0.006666666666666667 ===
= best_fin_err: 0.0439294231324323 =
= best_fin_err_no_noise: 0.00037233424914154473 =

=== disp_g: 0.06	add_noise: 0.01 ===
= best_fin_err: 0.09506196028083615 =
= best_fin_err_no_noise: 0.0009122486210627113 =

=== disp_g: 0.06	add_noise: 0.013333333333333334 ===
= best_fin_err: 0.1708898066842303 =
= best_fin_err_no_noise: 0.0007282811479143233 =

=== disp_g: 0.06	add_noise: 0.016666666666666666 ===
= best_fin_err: 0.27651652447690245 =
= best_fin_err_no_noise: 0.0033633901120651358 =

=== disp_g: 0.06	add_noise: 0.02 ===
= best_fin_err: 0.40853441304892735 =
= best_fin_err_no_noise: 0.002117204099514286 =

=== disp_g: 0.06	add_noise: 0.023333333333333334 ===
= best_fin_err: 0.5164417537236734 =
= best

In [147]:
fig = px.imshow((m_errors),
                labels=dict(y="disp_g", x="add_noise_disp", color="Error"),
                y=l_disp_g,
                x=l_add_noise_disp)

fig.show()

fig = px.imshow((m_errors_no_noise),
                labels=dict(y="disp_g", x="add_noise_disp", color="Error"),
                y=l_disp_g,
                x=l_add_noise_disp)

fig.show()

In [148]:
fig = px.imshow((m_delta_x),
                labels=dict(y="disp_g", x="add_noise_disp", color="Error"),
                y=l_disp_g,
                x=l_add_noise_disp)

fig.show()

fig = px.imshow((m_delta_y),
                labels=dict(y="disp_g", x="add_noise_disp", color="Error"),
                y=l_disp_g,
                x=l_add_noise_disp)

fig.show()

fig = px.imshow((m_delta_s),
                labels=dict(y="disp_g", x="add_noise_disp", color="Error"),
                y=l_disp_g,
                x=l_add_noise_disp)

fig.show()

In [149]:
trash_hold = 0.3
m_delta_s_1 = np.multiply(m_delta_s, (m_delta_s<trash_hold))


fig = px.imshow((m_delta_s_1),
                labels=dict(y="disp_g", x="add_noise_disp", color="Error"),
                y=l_disp_g,
                x=l_add_noise_disp)

fig.show()

In [153]:
disp_g = 0.12#0.092
ampl_gaus_noise = 0
add_noise_disp = 0.023

init_sol = [0.3, 0.6, disp_g, 
            0.5, 0.8, disp_g,
            0.7, 0.7, disp_g,
            0.5, ampl_gaus_noise, 0.3]

bounds = [[0,1], [0,1], [0,1], 
          [0,1], [0,1], [0,1],
          [0,1], [0,1], [0,1]]

sol, fin_err, fin_err_no_noise = mult_exper_2fit(disp_g, ampl_gaus_noise, bounds = bounds, add_noise_disp = add_noise_disp, num_launches=3)


print(f'fin_err: {fin_err}\fin_err_no_noise: {fin_err_no_noise}\tsol: {sol}')

init_spec, X = EvalSol(init_sol, add_noise_disp=add_noise_disp)
fin_spec, X = EvalSol(sol)
DrawApprox(init_spec, fin_spec, X, sol)
DrawApprox(init_spec, fin_spec, X, init_sol)


=== disp_g: 0.12	add_noise: 0.023 ===


C:\Users\Gavriil\AppData\Local\Temp\ipykernel_10008\885390838.py:3: RuntimeWarning:

divide by zero encountered in scalar divide

C:\Users\Gavriil\AppData\Local\Temp\ipykernel_10008\885390838.py:3: RuntimeWarning:

invalid value encountered in scalar divide



= best_fin_err: 0.5232478983435846 =
= best_fin_err_no_noise: 0.0041649431461484795 =
fin_err: 0.5232478983435846in_err_no_noise: 0.0041649431461484795	sol: [0.3052417429570237, 0.6213505761750626, 0.12191152058114153, 0.5076246439855627, 0.8041816226031149, 0.11924430553834144, 0.7055475331196308, 0.6797624545776796, 0.11823377171221928]


# 5-е приближение.
То же, что в 4-ой, только без x0=init_sol в нулевом приближении

In [157]:
'''l_disp_g = [0.1, 0.2, 0.3]
l_ampl_noise = [0.05, 0.1, 0.15, 0.2]
'''

l_disp_g = np.linspace(0.06, 0.12, 16)
ampl_gaus_noise = 0
l_add_noise_disp = np.linspace(0, 0.05, 16)

bounds = [[0,1], [0,1], [0,1], 
          [0,1], [0,1], [0,1],
          [0,1], [0,1], [0,1]]


l_errors = []
l_errors_no_noise = []
l_delta_x, l_delta_y, l_delta_s = [],[],[]

for disp_g, add_noise_disp in itertools.product(l_disp_g, l_add_noise_disp):
    best_sol, best_fin_err, best_fin_err_no_noise, delta_x, delta_y, delta_s = mult_exper_3(disp_g, ampl_gaus_noise, bounds = bounds, add_noise_disp = add_noise_disp, num_launches=5)
    l_errors.append(best_fin_err)
    l_errors_no_noise.append(best_fin_err_no_noise)

    l_delta_x.append(delta_x)
    l_delta_y.append(delta_y)
    l_delta_s.append(delta_s)

m_errors = np.array(l_errors).reshape(len(l_disp_g), len(l_add_noise_disp))
m_errors_no_noise = np.array(l_errors_no_noise).reshape(len(l_disp_g), len(l_add_noise_disp))

m_delta_x = np.array(l_delta_x).reshape(len(l_disp_g), len(l_add_noise_disp))
m_delta_y = np.array(l_delta_y).reshape(len(l_disp_g), len(l_add_noise_disp))
m_delta_s = np.array(l_delta_s).reshape(len(l_disp_g), len(l_add_noise_disp))


=== disp_g: 0.06	add_noise: 0.0 ===


C:\Users\Gavriil\AppData\Local\Temp\ipykernel_10008\885390838.py:3: RuntimeWarning:

divide by zero encountered in scalar divide

C:\Users\Gavriil\AppData\Local\Temp\ipykernel_10008\885390838.py:3: RuntimeWarning:

invalid value encountered in scalar divide



= best_fin_err: 4.723841663165803e-12 =
= best_fin_err_no_noise: 4.723841663165803e-12 =

=== disp_g: 0.06	add_noise: 0.0033333333333333335 ===
= best_fin_err: 9.469730011985673 =
= best_fin_err_no_noise: 9.465689164710334 =

=== disp_g: 0.06	add_noise: 0.006666666666666667 ===
= best_fin_err: 0.04576180241595625 =
= best_fin_err_no_noise: 0.00044379964433980377 =

=== disp_g: 0.06	add_noise: 0.01 ===
= best_fin_err: 0.09562314617357305 =
= best_fin_err_no_noise: 0.0009593034525904575 =

=== disp_g: 0.06	add_noise: 0.013333333333333334 ===
= best_fin_err: 0.16807476229496743 =
= best_fin_err_no_noise: 0.0022656513144317563 =

=== disp_g: 0.06	add_noise: 0.016666666666666666 ===
= best_fin_err: 0.28006534251327836 =
= best_fin_err_no_noise: 0.008437997527559502 =

=== disp_g: 0.06	add_noise: 0.02 ===
= best_fin_err: 9.673602137078197 =
= best_fin_err_no_noise: 9.466920187163069 =

=== disp_g: 0.06	add_noise: 0.023333333333333334 ===
= best_fin_err: 0.5270406724803478 =
= best_fin_err_no

In [158]:
fig = px.imshow((m_errors),
                labels=dict(y="disp_g", x="add_noise_disp", color="Error"),
                y=l_disp_g,
                x=l_add_noise_disp)

fig.show()

fig = px.imshow((m_errors_no_noise),
                labels=dict(y="disp_g", x="add_noise_disp", color="Error"),
                y=l_disp_g,
                x=l_add_noise_disp)

fig.show()

In [159]:
fig = px.imshow((m_delta_x),
                labels=dict(y="disp_g", x="add_noise_disp", color="Error"),
                y=l_disp_g,
                x=l_add_noise_disp)

fig.show()

fig = px.imshow((m_delta_y),
                labels=dict(y="disp_g", x="add_noise_disp", color="Error"),
                y=l_disp_g,
                x=l_add_noise_disp)

fig.show()

fig = px.imshow((m_delta_s),
                labels=dict(y="disp_g", x="add_noise_disp", color="Error"),
                y=l_disp_g,
                x=l_add_noise_disp)

fig.show()

In [160]:
disp_g = 0.12#0.092
ampl_gaus_noise = 0
add_noise_disp = 0.023

init_sol = [0.3, 0.6, disp_g, 
            0.5, 0.8, disp_g,
            0.7, 0.7, disp_g,
            0.5, ampl_gaus_noise, 0.3]

bounds = [[0,1], [0,1], [0,1], 
          [0,1], [0,1], [0,1],
          [0,1], [0,1], [0,1]]

sol, fin_err, fin_err_no_noise = mult_exper_2fit(disp_g, ampl_gaus_noise, bounds = bounds, add_noise_disp = add_noise_disp, num_launches=3)


print(f'fin_err: {fin_err}\fin_err_no_noise: {fin_err_no_noise}\tsol: {sol}')

init_spec, X = EvalSol(init_sol, add_noise_disp=add_noise_disp)
fin_spec, X = EvalSol(sol)
DrawApprox(init_spec, fin_spec, X, sol)
DrawApprox(init_spec, fin_spec, X, init_sol)


=== disp_g: 0.12	add_noise: 0.023 ===


C:\Users\Gavriil\AppData\Local\Temp\ipykernel_10008\885390838.py:3: RuntimeWarning:

invalid value encountered in scalar divide

C:\Users\Gavriil\AppData\Local\Temp\ipykernel_10008\885390838.py:3: RuntimeWarning:

divide by zero encountered in scalar divide



= best_fin_err: 0.500258639017423 =
= best_fin_err_no_noise: 0.0052080458502946 =
fin_err: 0.500258639017423in_err_no_noise: 0.0052080458502946	sol: [0.716943915798284, 0.5379343619366207, 0.11713702651192176, 0.2772701451556346, 0.419803437406616, 0.11444795321294304, 0.4972057395263895, 0.9602410918181981, 0.14629132532447547]


# 6-е приближение.
Вместо аддтивного шума используем гауссов шум

In [184]:
'''l_disp_g = [0.1, 0.2, 0.3]
l_ampl_noise = [0.05, 0.1, 0.15, 0.2]
'''

l_disp_g = np.linspace(0.06, 0.12, 16)
l_ampl_gaus_noise = np.linspace(0, 0.05, 16)
add_noise_disp = 0

bounds = [[0,1], [0,1], [0,1], 
          [0,1], [0,1], [0,1],
          [0,1], [0,1], [0,1]]


l_errors = []
l_errors_no_noise = []
l_delta_x, l_delta_y, l_delta_s = [],[],[]

for disp_g, ampl_gaus_noise in itertools.product(l_disp_g, l_ampl_gaus_noise):
    best_sol, best_fin_err, best_fin_err_no_noise, delta_x, delta_y, delta_s = mult_exper_3(disp_g, ampl_gaus_noise, bounds = bounds, add_noise_disp = add_noise_disp, num_launches=5)
    l_errors.append(best_fin_err)
    l_errors_no_noise.append(best_fin_err_no_noise)

    l_delta_x.append(delta_x)
    l_delta_y.append(delta_y)
    l_delta_s.append(delta_s)

m_errors = np.array(l_errors).reshape(len(l_disp_g), len(l_add_noise_disp))
m_errors_no_noise = np.array(l_errors_no_noise).reshape(len(l_disp_g), len(l_add_noise_disp))

m_delta_x = np.array(l_delta_x).reshape(len(l_disp_g), len(l_add_noise_disp))
m_delta_y = np.array(l_delta_y).reshape(len(l_disp_g), len(l_add_noise_disp))
m_delta_s = np.array(l_delta_s).reshape(len(l_disp_g), len(l_add_noise_disp))


=== disp_g: 0.06	ampl_noise: 0.0	add_noise: 0 ===


C:\Users\Gavriil\AppData\Local\Temp\ipykernel_10008\1965247583.py:3: RuntimeWarning:

divide by zero encountered in scalar divide

C:\Users\Gavriil\AppData\Local\Temp\ipykernel_10008\1965247583.py:3: RuntimeWarning:

invalid value encountered in scalar divide



= best_fin_err: 11.650811365287405 =
= best_fin_err_no_noise: 11.650811365287405 =

=== disp_g: 0.06	ampl_noise: 0.0033333333333333335	add_noise: 0 ===
= best_fin_err: 0.0004418540081495717 =
= best_fin_err_no_noise: 0.0004418540081495717 =

=== disp_g: 0.06	ampl_noise: 0.006666666666666667	add_noise: 0 ===
= best_fin_err: 9.440694690685957 =
= best_fin_err_no_noise: 9.440694690685957 =

=== disp_g: 0.06	ampl_noise: 0.01	add_noise: 0 ===
= best_fin_err: 0.003946403347276209 =
= best_fin_err_no_noise: 0.003946403347276209 =

=== disp_g: 0.06	ampl_noise: 0.013333333333333334	add_noise: 0 ===
= best_fin_err: 0.0069888077320219965 =
= best_fin_err_no_noise: 0.0069888077320219965 =

=== disp_g: 0.06	ampl_noise: 0.016666666666666666	add_noise: 0 ===
= best_fin_err: 0.010877685747500105 =
= best_fin_err_no_noise: 0.010877685747500105 =

=== disp_g: 0.06	ampl_noise: 0.02	add_noise: 0 ===
= best_fin_err: 11.580065484176718 =
= best_fin_err_no_noise: 11.580065484176718 =

=== disp_g: 0.06	ampl_n

In [193]:
fig = px.imshow((m_errors),
                labels=dict(y="disp_g", x="l_ampl_gaus_noise", color="Error"),
                y=l_disp_g,
                x=l_ampl_gaus_noise)

fig.show()

fig = px.imshow((m_errors_no_noise),
                labels=dict(y="disp_g", x="l_ampl_gaus_noise", color="Error"),
                y=l_disp_g,
                x=l_ampl_gaus_noise)

fig.show()

In [195]:
trash_hold = 0.3
m_errors_1 = np.multiply(m_errors, (m_errors<trash_hold))


fig = px.imshow((m_errors_1),
                labels=dict(y="disp_g", x="ampl_gaus_noise", color="Error"),
                y=l_disp_g,
                x=l_ampl_gaus_noise)

fig.show()

In [188]:
fig = px.imshow((m_delta_x),
                labels=dict(y="disp_g", x="ampl_gaus_noise", color="Error"),
                y=l_disp_g,
                x=l_ampl_gaus_noise)

fig.show()

fig = px.imshow((m_delta_y),
                labels=dict(y="disp_g", x="ampl_gaus_noise", color="Error"),
                y=l_disp_g,
                x=l_ampl_gaus_noise)

fig.show()

fig = px.imshow((m_delta_s),
                labels=dict(y="disp_g", x="ampl_gaus_noise", color="Error"),
                y=l_disp_g,
                x=l_ampl_gaus_noise)

fig.show()

In [196]:
disp_g = 0.07#0.092
ampl_gaus_noise = 0.023
add_noise_disp = 0

init_sol = [0.3, 0.6, disp_g, 
            0.5, 0.8, disp_g,
            0.7, 0.7, disp_g,
            0.5, ampl_gaus_noise, 0.3]

bounds = [[0,1], [0,1], [0,1], 
          [0,1], [0,1], [0,1],
          [0,1], [0,1], [0,1]]

sol, fin_err, fin_err_no_noise,x,y,d = mult_exper_3(disp_g, ampl_gaus_noise, bounds = bounds, add_noise_disp = add_noise_disp, num_launches=3)


print(f'fin_err: {fin_err}\fin_err_no_noise: {fin_err_no_noise}\tsol: {sol}')

init_spec, X = EvalSol(init_sol, add_noise_disp=add_noise_disp)
fin_spec, X = EvalSol(sol)
DrawApprox(init_spec, fin_spec, X, sol)
DrawApprox(init_spec, fin_spec, X, init_sol)


=== disp_g: 0.07	ampl_noise: 0.023	add_noise: 0 ===


C:\Users\Gavriil\AppData\Local\Temp\ipykernel_10008\1965247583.py:3: RuntimeWarning:

invalid value encountered in scalar divide

C:\Users\Gavriil\AppData\Local\Temp\ipykernel_10008\1965247583.py:3: RuntimeWarning:

divide by zero encountered in scalar divide



= best_fin_err: 0.013503082764232125 =
= best_fin_err_no_noise: 0.013503082764232125 =
fin_err: 0.013503082764232125in_err_no_noise: 0.013503082764232125	sol: [0.3010324726133302, 0.6179763341951869, 0.07232752051054779, 0.6991247689687524, 0.7179630343952883, 0.0719871830776323, 0.5000121939291031, 0.8167006903864513, 0.06881146434653965]


In [197]:
x,y,d

(0.0006399658578936281, 0.017546686325642196, 0.0018344130805468123)

In [172]:
init_sol[:-3], sol

([0.3, 0.6, 0.12, 0.5, 0.8, 0.12, 0.7, 0.7, 0.12],
 [0.5002184820302141,
  0.5986406056813925,
  0.10746612453497613,
  0.3199272436296138,
  0.7158042444658537,
  0.1275988233490288,
  0.6832451553596881,
  0.8127973112929463,
  0.12644098028035516])

In [173]:
np.abs(np.array(init_sol[:-3])-sol)

array([0.20021848, 0.00135939, 0.01253388, 0.18007276, 0.08419576,
       0.00759882, 0.01675484, 0.11279731, 0.00644098])

# 7-е приближение.
Нижний прямоугольник из прошлого эксперимента.

In [202]:
'''l_disp_g = [0.1, 0.2, 0.3]
l_ampl_noise = [0.05, 0.1, 0.15, 0.2]
'''

l_disp_g = np.linspace(0.075, 0.12, 16)
l_ampl_gaus_noise = np.linspace(0, 0.05, 16)
add_noise_disp = 0

bounds = [[0,1], [0,1], [0,1], 
          [0,1], [0,1], [0,1],
          [0,1], [0,1], [0,1]]


l_errors = []
l_errors_no_noise = []
l_delta_x, l_delta_y, l_delta_s = [],[],[]

for disp_g, ampl_gaus_noise in itertools.product(l_disp_g, l_ampl_gaus_noise):
    best_sol, best_fin_err, best_fin_err_no_noise, delta_x, delta_y, delta_s = mult_exper_3(disp_g, ampl_gaus_noise, bounds = bounds, add_noise_disp = add_noise_disp, num_launches=15)
    l_errors.append(best_fin_err)
    l_errors_no_noise.append(best_fin_err_no_noise)

    l_delta_x.append(delta_x)
    l_delta_y.append(delta_y)
    l_delta_s.append(delta_s)

m_errors = np.array(l_errors).reshape(len(l_disp_g), len(l_add_noise_disp))
m_errors_no_noise = np.array(l_errors_no_noise).reshape(len(l_disp_g), len(l_add_noise_disp))

m_delta_x = np.array(l_delta_x).reshape(len(l_disp_g), len(l_add_noise_disp))
m_delta_y = np.array(l_delta_y).reshape(len(l_disp_g), len(l_add_noise_disp))
m_delta_s = np.array(l_delta_s).reshape(len(l_disp_g), len(l_add_noise_disp))


=== disp_g: 0.075	ampl_noise: 0.0	add_noise: 0 ===


C:\Users\Gavriil\AppData\Local\Temp\ipykernel_10008\1965247583.py:3: RuntimeWarning:

divide by zero encountered in scalar divide

C:\Users\Gavriil\AppData\Local\Temp\ipykernel_10008\1965247583.py:3: RuntimeWarning:

invalid value encountered in scalar divide



= best_fin_err: 1.1989600529782043e-11 =
= best_fin_err_no_noise: 1.1989600529782043e-11 =

=== disp_g: 0.075	ampl_noise: 0.0033333333333333335	add_noise: 0 ===
= best_fin_err: 0.0002284065150757531 =
= best_fin_err_no_noise: 0.005706599793745899 =

=== disp_g: 0.075	ampl_noise: 0.006666666666666667	add_noise: 0 ===
= best_fin_err: 0.0009070958713531451 =
= best_fin_err_no_noise: 0.02283965286723419 =

=== disp_g: 0.075	ampl_noise: 0.01	add_noise: 0 ===
= best_fin_err: 0.0020263006102034502 =
= best_fin_err_no_noise: 0.05141808588152022 =

=== disp_g: 0.075	ampl_noise: 0.013333333333333334	add_noise: 0 ===
= best_fin_err: 0.003576294826924907 =
= best_fin_err_no_noise: 0.09146212533303012 =

=== disp_g: 0.075	ampl_noise: 0.016666666666666666	add_noise: 0 ===
= best_fin_err: 0.005547399740849231 =
= best_fin_err_no_noise: 0.14299039293377558 =

=== disp_g: 0.075	ampl_noise: 0.02	add_noise: 0 ===
= best_fin_err: 0.00792998910816195 =
= best_fin_err_no_noise: 0.2060217457425792 =

=== dis

In [231]:
fig = px.imshow((m_errors),
                labels=dict(y="disp_g", x="ampl_gaus_noise", color="Error"),
                y=l_disp_g,
                x=l_ampl_gaus_noise)

fig.show()

fig = px.imshow((m_errors_no_noise),
                labels=dict(y="disp_g", x="ampl_gaus_noise", color="Error"),
                y=l_disp_g,
                x=l_ampl_gaus_noise)

fig.show()

In [216]:
np.max(m_errors_1)

0.0463338301421254

In [220]:
trash_hold = 0.3
m_errors_1 = np.multiply(m_errors, (m_errors<trash_hold))
#m_errors_1 = np.log(m_errors_1/np.max(m_errors_1))


fig = px.imshow((m_errors_1),
                labels=dict(y="disp_g", x="ampl_gaus_noise", color="Error"),
                y=l_disp_g,
                x=l_ampl_gaus_noise)

fig.show()

In [205]:
fig = px.imshow((m_delta_x),
                labels=dict(y="disp_g", x="ampl_gaus_noise", color="Error"),
                y=l_disp_g,
                x=l_ampl_gaus_noise)

fig.show()

fig = px.imshow((m_delta_y),
                labels=dict(y="disp_g", x="ampl_gaus_noise", color="Error"),
                y=l_disp_g,
                x=l_ampl_gaus_noise)

fig.show()

fig = px.imshow((m_delta_s),
                labels=dict(y="disp_g", x="ampl_gaus_noise", color="Error"),
                y=l_disp_g,
                x=l_ampl_gaus_noise)

fig.show()

In [227]:
ampl_gaus_noise = 0.04
disp_g = 0.075#0.092
add_noise_disp = 0

init_sol = [0.3, 0.6, disp_g, 
            0.5, 0.8, disp_g,
            0.7, 0.7, disp_g,
            0.5, ampl_gaus_noise, 0.3]

bounds = [[0,1], [0,1], [0,1], 
          [0,1], [0,1], [0,1],
          [0,1], [0,1], [0,1]]

sol, fin_err, fin_err_no_noise,x,y,d = mult_exper_3(disp_g, ampl_gaus_noise, bounds = bounds, add_noise_disp = add_noise_disp, num_launches=15)


print(f'fin_err: {fin_err}\fin_err_no_noise: {fin_err_no_noise}\tsol: {sol}')

init_spec, X = EvalSol(init_sol, add_noise_disp=add_noise_disp)
fin_spec, X = EvalSol(sol)
DrawApprox(init_spec, fin_spec, X, sol)
DrawApprox(init_spec, fin_spec, X, init_sol)


=== disp_g: 0.075	ampl_noise: 0.04	add_noise: 0 ===


C:\Users\Gavriil\AppData\Local\Temp\ipykernel_10008\1965247583.py:3: RuntimeWarning:

divide by zero encountered in scalar divide

C:\Users\Gavriil\AppData\Local\Temp\ipykernel_10008\1965247583.py:3: RuntimeWarning:

invalid value encountered in scalar divide



= best_fin_err: 0.030335475516924497 =
= best_fin_err_no_noise: 0.8268176124544745 =
fin_err: 0.030335475516924497in_err_no_noise: 0.8268176124544745	sol: [0.30338499075938985, 0.636292327214621, 0.07995996182804518, 0.5000598016839255, 0.8154272751950568, 0.0714698011648027, 0.6971581494100765, 0.7361358895861689, 0.07921389539787195]


In [228]:
ampl_gaus_noise = 0.04
disp_g = 0.084#0.092
add_noise_disp = 0

init_sol = [0.3, 0.6, disp_g, 
            0.5, 0.8, disp_g,
            0.7, 0.7, disp_g,
            0.5, ampl_gaus_noise, 0.3]

bounds = [[0,1], [0,1], [0,1], 
          [0,1], [0,1], [0,1],
          [0,1], [0,1], [0,1]]

sol, fin_err, fin_err_no_noise,x,y,d = mult_exper_3(disp_g, ampl_gaus_noise, bounds = bounds, add_noise_disp = add_noise_disp, num_launches=15)


print(f'fin_err: {fin_err}\fin_err_no_noise: {fin_err_no_noise}\tsol: {sol}')

init_spec, X = EvalSol(init_sol, add_noise_disp=add_noise_disp)
fin_spec, X = EvalSol(sol)
DrawApprox(init_spec, fin_spec, X, sol)
DrawApprox(init_spec, fin_spec, X, init_sol)


=== disp_g: 0.084	ampl_noise: 0.04	add_noise: 0 ===


C:\Users\Gavriil\AppData\Local\Temp\ipykernel_10008\1965247583.py:3: RuntimeWarning:

divide by zero encountered in scalar divide

C:\Users\Gavriil\AppData\Local\Temp\ipykernel_10008\1965247583.py:3: RuntimeWarning:

invalid value encountered in scalar divide



= best_fin_err: 0.016980562838202692 =
= best_fin_err_no_noise: 0.8394789084331118 =
fin_err: 0.016980562838202692in_err_no_noise: 0.8394789084331118	sol: [0.3074050728582138, 0.6523066901844242, 0.09071984181197872, 0.5001240450188442, 0.7772035849454714, 0.07737470413815865, 0.6938022894204063, 0.751688886496776, 0.08969206155768157]


In [229]:
ampl_gaus_noise = 0.04
disp_g = 0.093#0.092
add_noise_disp = 0

init_sol = [0.3, 0.6, disp_g, 
            0.5, 0.8, disp_g,
            0.7, 0.7, disp_g,
            0.5, ampl_gaus_noise, 0.3]

bounds = [[0,1], [0,1], [0,1], 
          [0,1], [0,1], [0,1],
          [0,1], [0,1], [0,1]]

sol, fin_err, fin_err_no_noise,x,y,d = mult_exper_3(disp_g, ampl_gaus_noise, bounds = bounds, add_noise_disp = add_noise_disp, num_launches=15)


print(f'fin_err: {fin_err}\fin_err_no_noise: {fin_err_no_noise}\tsol: {sol}')

init_spec, X = EvalSol(init_sol, add_noise_disp=add_noise_disp)
fin_spec, X = EvalSol(sol)
DrawApprox(init_spec, fin_spec, X, sol)
DrawApprox(init_spec, fin_spec, X, init_sol)


=== disp_g: 0.093	ampl_noise: 0.04	add_noise: 0 ===


C:\Users\Gavriil\AppData\Local\Temp\ipykernel_10008\1965247583.py:3: RuntimeWarning:

invalid value encountered in scalar divide

C:\Users\Gavriil\AppData\Local\Temp\ipykernel_10008\1965247583.py:3: RuntimeWarning:

divide by zero encountered in scalar divide



= best_fin_err: 0.008236235046342608 =
= best_fin_err_no_noise: 0.8473246753719594 =
fin_err: 0.008236235046342608in_err_no_noise: 0.8473246753719594	sol: [0.31282490839955174, 0.6770035166239283, 0.10156078997173523, 0.5002008018253118, 0.7161354516065065, 0.0830035622937389, 0.6892888061808392, 0.775497030376773, 0.10023792342659714]


In [230]:
ampl_gaus_noise = 0.04
disp_g = 0.114#0.092
add_noise_disp = 0

init_sol = [0.3, 0.6, disp_g, 
            0.5, 0.8, disp_g,
            0.7, 0.7, disp_g,
            0.5, ampl_gaus_noise, 0.3]

bounds = [[0,1], [0,1], [0,1], 
          [0,1], [0,1], [0,1],
          [0,1], [0,1], [0,1]]

sol, fin_err, fin_err_no_noise,x,y,d = mult_exper_3(disp_g, ampl_gaus_noise, bounds = bounds, add_noise_disp = add_noise_disp, num_launches=15)


print(f'fin_err: {fin_err}\fin_err_no_noise: {fin_err_no_noise}\tsol: {sol}')

init_spec, X = EvalSol(init_sol, add_noise_disp=add_noise_disp)
fin_spec, X = EvalSol(sol)
DrawApprox(init_spec, fin_spec, X, sol)
DrawApprox(init_spec, fin_spec, X, init_sol)


=== disp_g: 0.114	ampl_noise: 0.04	add_noise: 0 ===


C:\Users\Gavriil\AppData\Local\Temp\ipykernel_10008\1965247583.py:3: RuntimeWarning:

divide by zero encountered in scalar divide

C:\Users\Gavriil\AppData\Local\Temp\ipykernel_10008\1965247583.py:3: RuntimeWarning:

invalid value encountered in scalar divide



= best_fin_err: 0.0009074156385931041 =
= best_fin_err_no_noise: 0.8539249538970866 =
fin_err: 0.0009074156385931041in_err_no_noise: 0.8539249538970866	sol: [0.32630125872412447, 0.7493742907599439, 0.12560464481629563, 0.5003227480023634, 0.532009147800604, 0.09758676273964019, 0.678139733713552, 0.8439770825648272, 0.12377877231434686]
